## Analysing predictions of Universal Dependencies (POS TAGGING)

In [1]:
import pandas as pd

pd.options.display.max_rows = 100000
pd.set_option('display.max_colwidth', -1)


In [2]:
with open("dev-nl.tsv") as f:
    lines = f.read().split("\n")

all_sentences = []
all_tags = []
sentence = ""
sentene_tags = ""
i = 0
for line in lines:
#     if a sentence ended
    if line=="":
        i += 1
        all_sentences.append(sentence.strip())
        all_tags.append(sentene_tags.strip())
        sentence =""
        sentene_tags = ""
    else:
        word = line.split("\t")[0]
        tag = line.split("\t")[1]
        
        sentence += " "+word
        sentene_tags += " "+tag

In [3]:
zero_shot = False
if zero_shot:
    preds_name = "dev_nl_predictions_zeroshot.txt"
else:
    preds_name = "dev_nl_predictions.txt"

In [4]:
with open(preds_name) as f:
    lines = f.read().split("\n")

all_pred_tags = []
pred_tags = ""
for line in lines:
#     if a sentence ended
    if line=="":
        all_pred_tags.append(pred_tags.strip())
        pred_tags = ""
    else:
        pred_tags += " "+line

In [5]:
ud_pos = pd.DataFrame(data={"sentences":all_sentences,"ground_truth":all_tags,"predictions":all_pred_tags})

In [6]:
ud_pos.tail()

sentences  \
1389  Vandersteen wekte de sympathie op van zijn collega's en afdelingschef en mocht het vakblad van de slagers illustreren .                                                                                                
1390  Ook de wachtkamer en de personeels- en vergaderzalen mocht hij onder handen nemen .                                                                                                                                    
1391  Zo kwam hij in contact met J. Meuwissen , een Nederlander die sinds 1936 het blad Bravo uitgaf en op zoek was naar Vlaams en Nederlands tekentalent nu er geen Amerikaanse strips meer mochten gepubliceerd worden .   
1392  Vandersteen mocht nu wekelijks een pagina vol tekenen rond Â« Sindbad de zeerover Â» , Â« Thor de holbewoner Â» en Â« Lancelot Â» .                                                                                    
1393  Het waren stuk voor stuk erg onbeholpen , maar charmante strips die de lezers wel op de lachspieren werkten .                                                                                                          

                                                                                                                                                                         ground_truth  \
1389  PROPN VERB DET NOUN ADP ADP PRON NOUN CCONJ NOUN CCONJ AUX DET NOUN ADP DET NOUN VERB PUNCT                                                                                       
1390  ADV DET NOUN CCONJ DET X CCONJ NOUN AUX PRON ADP NOUN VERB PUNCT                                                                                                                  
1391  ADV VERB PRON ADP NOUN ADP PROPN PROPN PUNCT DET PROPN PRON ADP NUM DET NOUN PROPN VERB CCONJ ADP NOUN AUX ADP ADJ CCONJ ADJ NOUN SCONJ ADV DET ADJ NOUN ADV AUX VERB AUX PUNCT   
1392  PROPN AUX ADV ADJ DET NOUN ADJ VERB ADP PUNCT PROPN DET NOUN PUNCT PUNCT PUNCT PROPN DET NOUN PUNCT CCONJ PUNCT PROPN PUNCT PUNCT                                                 
1393  PRON AUX NOUN ADP NOUN ADJ ADJ PUNCT CCONJ ADJ NOUN PRON DET NOUN ADV ADP DET NOUN VERB PUNCT                                                                                     

                                                                                                                                                                        predictions  
1389  PROPN VERB DET NOUN ADP ADP PRON NOUN CCONJ NOUN CCONJ AUX DET NOUN ADP DET NOUN VERB PUNCT                                                                                    
1390  ADV DET NOUN CCONJ DET X CCONJ NOUN AUX PRON ADP NOUN VERB PUNCT                                                                                                               
1391  ADV VERB PRON ADP NOUN ADP PROPN PROPN PUNCT DET PROPN PRON ADP NUM DET NOUN PROPN VERB CCONJ ADP NOUN AUX ADP ADJ CCONJ ADJ NOUN ADV ADV DET ADJ NOUN ADV AUX VERB AUX PUNCT  
1392  PROPN AUX ADV ADJ DET NOUN ADJ VERB ADP PUNCT PROPN DET NOUN PUNCT PUNCT PUNCT PROPN DET NOUN PUNCT CCONJ PUNCT PROPN PUNCT PUNCT                                              
1393  PRON AUX NOUN ADP NOUN ADJ ADJ PUNCT CCONJ ADJ NOUN PRON DET NOUN ADV ADP DET NOUN VERB PUNCT

In [32]:
ud_pos[ud_pos.sentences.str.contains("de")]

sentences  \
1     De afgelopen week twijfelde ze nog of ze wel moest meedoen aan het NK .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      
2     Moeder Mien spoorde haar aan toch op te stappen .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
3     Tot halverwege de koers had Van Alebeek moeite om zich volledig te concentreren op de wedstrijd .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
5     Om ongelukken te voorkomen heb ik mezelf gedwongen om me alleen nog met de koers bezig te houden . ''                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
6     Veertig kilometer voor het einde ontstond een kopgroep met zes vrouwen .                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
7     Behalve Van Alebeek en haar ploeggenote Bertine Spijkerman was ook Saskia Kaagman uit de opleidingsploeg van Farm Frites meegesprongen .                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
8     Met venijnige demarrages matte de talentvolle Kaagman de concurrentie af .                                                                                                                                                                                                                                                                                                                                           

In [7]:
unique_tags = "ADJ ADP ADV AUX CCONJ DET INTJ NOUN NUM PART PRON PROPN PUNCT SCONJ SYM VERB X".split()

In [8]:
import numpy as np
confusion_matrix = np.zeros((len(unique_tags),len(unique_tags)))
# rows represent predicted values and columns represent actuals

In [60]:
total_tags = 0
incorrect_tags = 0
mistakes_df = {"predicted":[],"actual":[],"token":[],"sentence":[],"actual_tokens":[]}
for i in range(len(all_tags)):
    actual_sent = all_tags[i].split()
    pred_sent = all_pred_tags[i].split()
    assert len(actual_sent)==len(pred_sent),"Number of actual and predicted tags for the same sentence should be equal"
    for j in range(len(actual_sent)):
        if not actual_sent[j]==pred_sent[j]:
            mistakes_df["predicted"].append(pred_sent[j])
            mistakes_df["actual"].append(actual_sent[j])
            mistakes_df["token"].append(all_sentences[i].split()[j])
            mistakes_df["sentence"].append(all_sentences[i])
            mistakes_df["actual_tokens"].append(" ".join(actual_sent))
            
            confusion_matrix[unique_tags.index(pred_sent[j])][unique_tags.index(actual_sent[j])] += 1
            incorrect_tags += 1
        total_tags += 1
#     if incorrect_tags==5:
#         print("break")
#         break

In [61]:
mistakes_df = pd.DataFrame.from_dict(mistakes_df)

In [65]:
mistakes_df[(mistakes_df.actual=="PROPN")]

predicted actual              token  \
5    NOUN      PROPN  Zuid-Amerikanen     
12   NOUN      PROPN  Duitser             
19   NOUN      PROPN  Rabo's              
22   NOUN      PROPN  Rabo's              
25   NOUN      PROPN  Rabo's              
26   NOUN      PROPN  Boogerd             
27   ADJ       PROPN  Boogerd             
30   ADJ       PROPN  Zuid                
50   NOUN      PROPN  WOW                 
60   X         PROPN  Ad                  
61   X         PROPN  tuendam             
62   X         PROPN  fidem               
73   CCONJ     PROPN  en                  
74   DET       PROPN  de                  
75   NOUN      PROPN  Voederbietels       
90   NOUN      PROPN  Schreuders          
91   NOUN      PROPN  Schreuders          
112  ADJ       PROPN  Europese            
113  NOUN      PROPN  Commissie           
116  ADJ       PROPN  Europese            
117  NOUN      PROPN  Commissie           
122  ADJ       PROPN  Dwaze               
123  NOUN      PROPN  Moeders             
130  NOUN      PROPN  WK                  
131  NOUN      PROPN  WK                  
132  NOUN      PROPN  B-landen            
134  NOUN      PROPN  Duitser             
138  NOUN      PROPN  Warners             
139  NOUN      PROPN  WK                  
140  NOUN      PROPN  Duitser             
145  DET       PROPN  De                  
147  NOUN      PROPN  STA                 
154  NOUN      PROPN  WK                  
157  NOUN      PROPN  Italianen           
158  NOUN      PROPN  Italianen           
159  DET       PROPN  't                  
160  NOUN      PROPN  Gumbs               
162  NOUN      PROPN  Italianen           
163  NOUN      PROPN  Italianen           
173  NOUN      PROPN  Zuid-Amerikanen     
176  ADV       PROPN  Delmee              
178  NOUN      PROPN  Lurling             
188  ADJ       PROPN  Jong                
189  ADJ       PROPN  Jong                
192  NOUN      PROPN  Laffer-curve        
197  X         PROPN  Compassionate       
198  X         PROPN  Conservatism        
212  NOUN      PROPN  Kasteel             
213  NOUN      PROPN  Kasteel             
214  NOUN      PROPN  Kasteel             
215  NOUN      PROPN  Kasteel             
240  NOUN      PROPN  Aswoensdag          
241  NOUN      PROPN  Uitgeverij          
242  NOUN      PROPN  Uitgeverij          
246  NOUN      PROPN  Uitgeverij          
248  NOUN      PROPN  Uitgeverij          
295  NOUN      PROPN  Amerikanen          
303  DET       PROPN  De                  
304  ADJ       PROPN  Blauwe              
305  NOUN      PROPN  Lotus               
306  DET       PROPN  De                  
307  ADJ       PROPN  Blauwe              
308  NOUN      PROPN  Lotus               
314  NOUN      PROPN  Man                 
316  X         PROPN  Les                 
317  X         PROPN  vingt               
320  ADP       PROPN  voor                
344  X         PROPN  Fanfares            
345  X         PROPN  doctrinaires        
350  NOUN      PROPN  Museum              
351  ADP       PROPN  voor                
352  NOUN      PROPN  Kunsten             
359  X         PROPN  plume               
380  ADJ       PROPN  Chinees             
390  NOUN      PROPN  tuf-tuf-club        
408  NOUN      PROPN  Biggles             
409  X         PROPN  Tits                
414  NOUN      PROPN  Kaproen             
423  ADJ       PROPN  oud-Nederlands      
426  ADJ       PROPN  Vlaams/Nederlands   
436  NOUN      PROPN  Tits                
443  ADJ       PROPN  Heilig              
444  NOUN      PROPN  Graf                

                                                                                                                                                                                                                                                                                                                                                                                                       

How many words predicted as PROPN are capitalized?

In [58]:
mistakes_df[mistakes_df.predicted!=mistakes_df.actual].token.str[0].str.isupper().value_counts()

True     145
False    13 
Name: token, dtype: int64

In [59]:
mistakes_df

predicted actual                              token  \
0     PROPN     PROPN  NK                                  
1     PROPN     PROPN  Mien                                
2     PROPN     PROPN  Van                                 
3     PROPN     PROPN  Alebeek                             
4     PROPN     PROPN  Van                                 
5     PROPN     PROPN  Alebeek                             
6     PROPN     PROPN  Bertine                             
7     PROPN     PROPN  Spijkerman                          
8     PROPN     PROPN  Saskia                              
9     PROPN     PROPN  Kaagman                             
10    PROPN     PROPN  Farm                                
11    PROPN     PROPN  Frites                              
12    PROPN     PROPN  Kaagman                             
13    PROPN     PROPN  Van                                 
14    PROPN     PROPN  Alebeek                             
15    PROPN     PROPN  Zijlaard                            
16    PROPN     PROPN  Spijkerman                          
17    PROPN     PROPN  Van                                 
18    PROPN     PROPN  Moorsel                             
19    PROPN     PROPN  Yevgeny                             
20    PROPN     PROPN  Kafelnikov                          
21    PROPN     PROPN  Argentijn                           
22    PROPN     PROPN  Guillermo                           
23    PROPN     PROPN  Canas                               
24    PROPN     PROPN  Wimbledon                           
25    PROPN     PROPN  Amelie                              
26    PROPN     PROPN  Mauresmo                            
27    PROPN     PROPN  Tanasugarn                          
28    PROPN     PROPN  Canas                               
29    PROPN     PROPN  Rus                                 
30    PROPN     PROPN  Londen                              
31    PROPN     PROPN  Argentijn                           
32    PROPN     PROPN  Wimbledon                           
33    PROPN     PROPN  Zuid-Amerikaan                      
34    PROPN     PROPN  Grand                               
35    PROPN     PROPN  Slam                                
36    PROPN     PROPN  Rosmalen                            
37    PROPN     PROPN  Hewitt                              
38    PROPN     PROPN  Canas                               
39    PROPN     PROPN  Buenos                              
40    PROPN     PROPN  Aires                               
41    PROPN     PROPN  januari                             
42    PROPN     PROPN  Egypte                              
43    PROPN     PROPN  Afrikanen                           
44    PROPN     PROPN  Rosario                             
45    PROPN     PROPN  Nederlanders                        
46    PROPN     PROPN  Oranje                              
47    PROPN     PROPN  Van                                 
48    PROPN     PROPN  der                                 
49    PROPN     PROPN  Vaart                               
50    PROPN     PROPN  Heitinga                            
51    PROPN     PROPN  Van                                 
52    PROPN     PROPN  Gaal                                
53    PROPN     PROPN  Cordoba                             
54    PROPN     PROPN  Egypte                              
55    PROPN     PROPN  woensdag                            
56    PROPN     PROPN  Ghana                               
57    PROPN     PROPN  BraziliÃ«                           
58    PROPN     PROPN  Buenos                              
59    PROPN     PROPN  Aires                               
60    PROPN     PROPN  ArgentiniÃ«                         
61    PROPN     PROPN  Paraguay                            
62    PROPN     PROPN  Argentijnen                         
63    PROPN     PROPN  Frankrijk                           
64    PROPN     PROPN  Saviola                             
65    PROPN     PROPN  Paraguay              

Tokens predicted as proper nouns that are not uppercase

In [56]:
propn = mistakes_df[mistakes_df.predicted!=mistakes_df.actual].token.str[0]
mistakes_df[mistakes_df.predicted!=mistakes_df.actual].token[~propn.str.isupper()]

441     !       
505     van     
565     little  
833     meerkamp
1386    van     
1432    van     
1634    't      
1676    &       
1764    morte   
1997    het     
2091    en      
2312    en      
2376    't      
Name: token, dtype: object

In [12]:
from collections import defaultdict
top10_confused_tokens = mistakes_df.token.value_counts().index
for token in top10_confused_tokens:
    print(token)
    token_tags = defaultdict(int)
    display(mistakes_df[mistakes_df.token==token].actual.value_counts())
    for i,sentence in enumerate(all_sentences):
        words = sentence.split()
        for j,word in enumerate(words):
            if word==token:
                tag = all_tags[i].split()[j]
                token_tags[tag] += 1
    print(token_tags)

als


ADP      10
SCONJ    1 
Name: actual, dtype: int64

defaultdict(<class 'int'>, {'SCONJ': 27, 'ADP': 59})
De


DET      6
PROPN    3
Name: actual, dtype: int64

defaultdict(<class 'int'>, {'DET': 253, 'PROPN': 23})
Uitgeverij


...

defaultdict(<class 'int'>, {'ADV': 1, 'ADJ': 1})
Moeders


PROPN    1
Name: actual, dtype: int64

defaultdict(<class 'int'>, {'PROPN': 1, 'NOUN': 1})
Hogere


ADJ    1
Name: actual, dtype: int64

defaultdict(<class 'int'>, {'ADJ': 1})


In [13]:
mistakes_df.token.value_counts()

als                              11
De                               9 
Uitgeverij                       7 
was                              7 
werken                           6 
is                               6 
-                                6 
eerder                           6 
Vlaams                           6 
F1                               5 
juist                            4 
)                                4 
Italianen                        4 
(                                4 
Ridder                           4 
meer                             4 
Rode                             4 
Kasteel                          4 
WK                               4 
werd                             3 
van                              3 
Duitser                          3 
neer                             3 
Prijs                            3 
't                               3 
konden                           3 
en                               3 
Rabo's                      

In [35]:
ud_pos[ud_pos.sentences.str.contains("president")]

sentences  \
210  Op 1 juni reisde de Colombiaanse president Pastrana naar de Paraguayaanse hoofdstad AsunciÃ³n .                                                                                             
224  Zichtbaar geÃ«motioneerd en lijkbleek legde Mejia vrijdagavond in het bijzijn van president Pastrana een verklaring af voor de Colombiaanse televisie .                                     
488  Alsof het een weekend-uitje betrof , heeft de Amerikaanse vice-president Dick Cheney zaterdag ' even ' een operatie ondergaan .                                                             
516  Na een soortgelijke IsraÃ«lische wraakaanval op een Syrische positie buiten Beiroet in april , liet de Syrische president Assad waarschuwende geluiden horen , maar ondernam geen actie .   

                                                                                                                               ground_truth  \
210  ADP NUM PROPN VERB DET ADJ NOUN PROPN ADP DET ADJ NOUN PROPN PUNCT                                                                       
224  ADJ VERB CCONJ ADJ VERB PROPN NOUN ADP DET NOUN ADP NOUN PROPN DET NOUN ADP ADP DET ADJ NOUN PUNCT                                       
488  SCONJ PRON DET NOUN VERB PUNCT AUX DET ADJ NOUN PROPN PROPN PROPN PUNCT ADV PUNCT DET NOUN VERB PUNCT                                    
516  ADP DET ADJ ADJ NOUN ADP DET ADJ NOUN ADP PROPN ADP PROPN PUNCT VERB DET ADJ NOUN PROPN VERB NOUN VERB PUNCT CCONJ VERB DET NOUN PUNCT   

                                                                                                                                predictions  
210  ADP NUM PROPN VERB DET ADJ NOUN PROPN ADP DET ADJ NOUN PROPN PUNCT                                                                      
224  ADJ VERB CCONJ ADJ VERB PROPN NOUN ADP DET NOUN ADP NOUN PROPN DET NOUN ADP ADP DET ADJ NOUN PUNCT                                      
488  SCONJ PRON DET NOUN VERB PUNCT AUX DET ADJ NOUN PROPN PROPN PROPN PUNCT ADV PUNCT DET NOUN VERB PUNCT                                   
516  ADP DET ADJ ADJ NOUN ADP DET ADJ NOUN ADP PROPN ADP PROPN PUNCT VERB DET ADJ NOUN PROPN VERB NOUN VERB PUNCT CCONJ VERB DET NOUN PUNCT

In [34]:
mistakes_df[(mistakes_df.predicted=="PROPN")&(mistakes_df.actual=="NOUN")]

predicted actual                     token  \
32   PROPN     NOUN   FARC-rebellen              
33   PROPN     NOUN   FARC-rebellen              
34   PROPN     NOUN   FARC-woordvoerder          
56   PROPN     NOUN   Nobelprijswinnaar          
66   PROPN     NOUN   Geest                      
78   PROPN     NOUN   Aidsfonds                  
82   PROPN     NOUN   Aidsfonds                  
88   PROPN     NOUN   Partij                     
92   PROPN     NOUN   Bestuursdienst             
93   PROPN     NOUN   Telecommunicatie           
94   PROPN     NOUN   Post                       
95   PROPN     NOUN   Rijksluchtvaartdienst      
97   PROPN     NOUN   Bijlmerramp                
125  PROPN     NOUN   Vrijdag-akkoord            
126  PROPN     NOUN   Hezbollah-strijders        
135  PROPN     NOUN   Prijs                      
137  PROPN     NOUN   meerkamp                   
166  PROPN     NOUN   Goorbergh-tribune          
179  PROPN     NOUN   Lenstra-stadion            
184  PROPN     NOUN   Kartel                     
196  PROPN     NOUN   Paleoconservatisme         
216  PROPN     NOUN   Prijs                      
218  PROPN     NOUN   F1                         
219  PROPN     NOUN   F1                         
220  PROPN     NOUN   F1                         
224  PROPN     NOUN   Prijs                      
226  PROPN     NOUN   F1                         
227  PROPN     NOUN   F1                         
230  PROPN     NOUN   Zee                        
233  PROPN     NOUN   Vastentijd                 
239  PROPN     NOUN   Concilie                   
245  PROPN     NOUN   Blok                       
251  PROPN     NOUN   Uitgeverij                 
253  PROPN     NOUN   Uitgeverij                 
254  PROPN     NOUN   Troef                      
255  PROPN     NOUN   Uitgeverij                 
266  PROPN     NOUN   Scholieren                 
267  PROPN     NOUN   Actie                      
268  PROPN     NOUN   Groep                      
269  PROPN     NOUN   Volkspartij                
270  PROPN     NOUN   Pol&Soc                    
271  PROPN     NOUN   Faculteiten                
275  PROPN     NOUN   Handelsschool              
277  PROPN     NOUN   Blok                       
291  PROPN     NOUN   Instelling                 
292  PROPN     NOUN   Tegenstroom                
294  PROPN     NOUN   Project                    
298  PROPN     NOUN   Begraafplaats              
310  PROPN     NOUN   O.L.V.-college             
311  PROPN     NOUN   Onze-Lieve-Vrouwecollege   
313  PROPN     NOUN   Academie                   
322  PROPN     NOUN   Salon                      
331  PROPN     NOUN   Salon                      
333  PROPN     NOUN   Calvarie                   
334  PROPN     NOUN   Aureolen                   
356  PROPN     NOUN   Lampenist                  
360  PROPN     NOUN   Olie                       
366  PROPN     NOUN   Aureolen                   
367  PROPN     NOUN   Carnaval                   
370  PROPN     NOUN   Baron                      
379  PROPN     NOUN   Sirene                     
392  PROPN     NOUN   Bruegel                    
393  PROPN     NOUN   Bruegel                    
397  PROPN     NOUN   Volk                       
399  PROPN     NOUN   Volkske                    
400  PROPN     NOUN   Kapoentje                  
407  PROPN     NOUN   Ridder                     
413  PROPN     NOUN   Ridder                     
418  PROPN     NOUN   Nationaal-Socialist        
422  PROPN     NOUN   Dag                        
424  PROPN     NOUN   Wiskeverhalen              
428  PROPN     NOUN   Reeks                      
435  PROPN     NOUN   Ridder                     
439  PROPN     NOUN   Prinske                    
442  PROPN     NOUN   Ridder                     
446  PROPN     NOUN   Akademie                   
448  PROPN     NOUN   Kunsten                    
451  PROPN     NOUN   Dag                        

                                                     

In [14]:
conf_df = pd.DataFrame(data=confusion_matrix,index=unique_tags,columns=unique_tags)

#### How many times each tag is misclassified

In [15]:
conf_count = pd.DataFrame()
conf_count["count"] = conf_df.sum().sort_values(ascending=False); 
conf_count["percent"] = conf_count/conf_count.sum()
conf_count[:10]

count   percent
NOUN   103.0  0.227373
PROPN  83.0   0.183223
ADJ    63.0   0.139073
VERB   50.0   0.110375
X      34.0   0.075055
SYM    25.0   0.055188
DET    21.0   0.046358
ADP    18.0   0.039735
ADV    17.0   0.037528
NUM    15.0   0.033113

In [21]:
conf_count.to_csv("conf_count_sup.csv",index_label="tag")

In [29]:
sparse_conf_df = conf_df.reset_index().melt(id_vars="index",var_name="actual",value_name="count").rename(columns={"index":"pred"})
sparse_conf_df["percent"] = sparse_conf_df["count"]/sparse_conf_df["count"].sum()
sparse_conf_df = sparse_conf_df.sort_values(by="count",ascending=False);sparse_conf_df

pred actual  count   percent
130  PROPN  NOUN   78.0   0.172185
194  NOUN   PROPN  50.0   0.110375
283  PROPN  X      30.0   0.066225
11   PROPN  ADJ    26.0   0.057395
255  ADJ    VERB   24.0   0.052980
258  AUX    VERB   18.0   0.039735
250  PUNCT  SYM    17.0   0.037528
2    ADV    ADJ    14.0   0.030905
150  SYM    NUM    14.0   0.030905
187  ADJ    PROPN  13.0   0.028698
134  VERB   NOUN   12.0   0.026490
15   VERB   ADJ    12.0   0.026490
30   SCONJ  ADP    11.0   0.024283
203  X      PROPN  11.0   0.024283
96   PROPN  DET    9.0    0.019868
66   VERB   AUX    8.0    0.017660
7    NOUN   ADJ    7.0    0.015453
34   ADJ    ADV    6.0    0.013245
119  ADJ    NOUN   6.0    0.013245
249  PROPN  SYM    5.0    0.011038
262  NOUN   VERB   5.0    0.011038
192  DET    PROPN  5.0    0.011038
87   ADV    DET    4.0    0.008830
44   PRON   ADV    4.0    0.008830
19   ADV    ADP    4.0    0.008830
175  DET    PRON   3.0    0.006623
28   PROPN  ADP    3.0    0.006623
266  PROPN  VERB   3.0    0.006623
95   PRON   DET    3.0    0.006623
35   ADP    ADV    3.0    0.006623
85   ADJ    DET    3.0    0.006623
223  ADV    SCONJ  2.0    0.004415
79   PROPN  CCONJ  2.0    0.004415
245  NOUN   SYM    2.0    0.004415
188  ADP    PROPN  2.0    0.004415
121  ADV    NOUN   2.0    0.004415
181  PROPN  PRON   2.0    0.004415
39   DET    ADV    2.0    0.004415
135  X      NOUN   2.0    0.004415
1    ADP    ADJ    2.0    0.004415
170  ADJ    PRON   2.0    0.004415
172  ADV    PRON   2.0    0.004415
5    DET    ADJ    2.0    0.004415
231  PRON   SCONJ  1.0    0.002208
93   NUM    DET    1.0    0.002208
189  ADV    PROPN  1.0    0.002208
127  NUM    NOUN   1.0    0.002208
279  NOUN   X      1.0    0.002208
246  NUM    SYM    1.0    0.002208
284  PUNCT  X      1.0    0.002208
274  ADV    X      1.0    0.002208
273  ADP    X      1.0    0.002208
120  ADP    NOUN   1.0    0.002208
133  SYM    NOUN   1.0    0.002208
99   SYM    DET    1.0    0.002208
106  CCONJ  INTJ   1.0    0.002208
47   SCONJ  ADV    1.0    0.002208
143  NOUN   NUM    1.0    0.002208
222  ADP    SCONJ  1.0    0.002208
41   NOUN   ADV    1.0    0.002208
191  CCONJ  PROPN  1.0    0.002208
210  INTJ   PUNCT  0.0    0.000000
198  PROPN  PROPN  0.0    0.000000
199  PUNCT  PROPN  0.0    0.000000
209  DET    PUNCT  0.0    0.000000
197  PRON   PROPN  0.0    0.000000
200  SCONJ  PROPN  0.0    0.000000
208  CCONJ  PUNCT  0.0    0.000000
204  ADJ    PUNCT  0.0    0.000000
201  SYM    PROPN  0.0    0.000000
206  ADV    PUNCT  0.0    0.000000
202  VERB   PROPN  0.0    0.000000
205  ADP    PUNCT  0.0    0.000000
207  AUX    PUNCT  0.0    0.000000
0    ADJ    ADJ    0.0    0.000000
196  PART   PROPN  0.0    0.000000
195  NUM    PROPN  0.0    0.000000
164  PROPN  PART   0.0    0.000000
165  PUNCT  PART   0.0    0.000000
166  SCONJ  PART   0.0    0.000000
167  SYM    PART   0.0    0.000000
168  VERB   PART   0.0    0.000000
169  X      PART   0.0    0.000000
171  ADP    PRON   0.0    0.000000
173  AUX    PRON   0.0    0.000000
174  CCONJ  PRON   0.0    0.000000
176  INTJ   PRON   0.0    0.000000
177  NOUN   PRON   0.0    0.000000
178  NUM    PRON   0.0    0.000000
179  PART   PRON   0.0    0.000000
180  PRON   PRON   0.0    0.000000
182  PUNCT  PRON   0.0    0.000000
183  SCONJ  PRON   0.0    0.000000
184  SYM    PRON   0.0    0.000000
185  VERB   PRON   0.0    0.000000
186  X      PRON   0.0    0.000000
190  AUX    PROPN  0.0    0.000000
193  INTJ   PROPN  0.0    0.000000
211  NOUN   PUNCT  0.0    0.000000
225  CCONJ  SCONJ  0.0    0.000000
212  NUM    PUNCT  0.0    0.000000
248  PRON   SYM    0.0    0.000000
252  SYM    SYM    0.0    0.000000
253  VERB   SYM    0.0    0.000000
254  X      SYM    0.0    0.000000
256  ADP    VERB   0.0    0.000000
257  ADV    VERB   0.0    0.000000
259  CCONJ  VERB   0.0    0.000000
260  DET    VERB   0.0    0.000000
261  INTJ   VERB   0.0    0.000000
263  NUM    VERB   0.0    0.000000
264  PART   VERB   0.0    0.000000
265  PRON   VERB   0.0    0.000000
267  PUNCT  VERB

In [30]:
sparse_conf_df.to_csv("conf_pairs_sup.csv",index=False)

In [18]:
total_tags, incorrect_tags

(22938, 453)

In [19]:
print("Accuracy: ",(total_tags-incorrect_tags)/total_tags)

Accuracy:  0.9802511116923882


In [20]:
ud_pos.tail()

sentences  \
1389  Vandersteen wekte de sympathie op van zijn collega's en afdelingschef en mocht het vakblad van de slagers illustreren .                                                                                                
1390  Ook de wachtkamer en de personeels- en vergaderzalen mocht hij onder handen nemen .                                                                                                                                    
1391  Zo kwam hij in contact met J. Meuwissen , een Nederlander die sinds 1936 het blad Bravo uitgaf en op zoek was naar Vlaams en Nederlands tekentalent nu er geen Amerikaanse strips meer mochten gepubliceerd worden .   
1392  Vandersteen mocht nu wekelijks een pagina vol tekenen rond Â« Sindbad de zeerover Â» , Â« Thor de holbewoner Â» en Â« Lancelot Â» .                                                                                    
1393  Het waren stuk voor stuk erg onbeholpen , maar charmante strips die de lezers wel op de lachspieren werkten .                                                                                                          

                                                                                                                                                                         ground_truth  \
1389  PROPN VERB DET NOUN ADP ADP PRON NOUN CCONJ NOUN CCONJ AUX DET NOUN ADP DET NOUN VERB PUNCT                                                                                       
1390  ADV DET NOUN CCONJ DET X CCONJ NOUN AUX PRON ADP NOUN VERB PUNCT                                                                                                                  
1391  ADV VERB PRON ADP NOUN ADP PROPN PROPN PUNCT DET PROPN PRON ADP NUM DET NOUN PROPN VERB CCONJ ADP NOUN AUX ADP ADJ CCONJ ADJ NOUN SCONJ ADV DET ADJ NOUN ADV AUX VERB AUX PUNCT   
1392  PROPN AUX ADV ADJ DET NOUN ADJ VERB ADP PUNCT PROPN DET NOUN PUNCT PUNCT PUNCT PROPN DET NOUN PUNCT CCONJ PUNCT PROPN PUNCT PUNCT                                                 
1393  PRON AUX NOUN ADP NOUN ADJ ADJ PUNCT CCONJ ADJ NOUN PRON DET NOUN ADV ADP DET NOUN VERB PUNCT                                                                                     

                                                                                                                                                                        predictions  
1389  PROPN VERB DET NOUN ADP ADP PRON NOUN CCONJ NOUN CCONJ AUX DET NOUN ADP DET NOUN VERB PUNCT                                                                                    
1390  ADV DET NOUN CCONJ DET X CCONJ NOUN AUX PRON ADP NOUN VERB PUNCT                                                                                                               
1391  ADV VERB PRON ADP NOUN ADP PROPN PROPN PUNCT DET PROPN PRON ADP NUM DET NOUN PROPN VERB CCONJ ADP NOUN AUX ADP ADJ CCONJ ADJ NOUN ADV ADV DET ADJ NOUN ADV AUX VERB AUX PUNCT  
1392  PROPN AUX ADV ADJ DET NOUN ADJ VERB ADP PUNCT PROPN DET NOUN PUNCT PUNCT PUNCT PROPN DET NOUN PUNCT CCONJ PUNCT PROPN PUNCT PUNCT                                              
1393  PRON AUX NOUN ADP NOUN ADJ ADJ PUNCT CCONJ ADJ NOUN PRON DET NOUN ADV ADP DET NOUN VERB PUNCT